In [4]:
import re
import pymysql
import numpy as np
import pandas as pd

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all" 

# 数据合并

In [2]:
#这份是由工作室提供的用户数据
users_1 = pd.read_csv(r'douban_book_users.txt', delimiter="\t")
users_1.head(10)

id nickname  read_num  \
0    1000287     耶律王其        95   
1    1023147      殊不方       206   
2  103031697     一潭死水       115   
3    1032498      蜜三刀       631   
4  113496629    虫子凹二千       146   
5  115818974     空心汤团        45   
6    1170905  幸福超市总经理      1917   
7   11850970   柏拉图斯特拉       949   
8  120452199     蓝色的鲸       362   
9  122612759     鸡兔同班      1321   

                                 read_book_and_score  
0  {'牧齋有學集（全三冊）': 4, '回鹘文买卖契约译注': 3, '清朝统一准噶尔史实研究...  
1  {'卡斯蒂利亚的田野：马查多诗选': 2, '艾吕雅诗选': 2, '想象一朵未来的玫瑰':...  
2  {'波斯人信札': 4, '阿马罗神父的罪恶': 4, '理智与情感（木刻插图本）': 4,...  
3  {'牲人祭': 3, '正定歌谣': 5, '中国民族史（上册）': 5, '地狱书单': ...  
4  {'救猫咪': 4, '牧羊少年奇幻之旅': 3, '月亮与六便士': 5, '山海经': ...  
5  {'我们生活的故事': 4, '优雅': 2, 'ADC年鑑2010 TOKYO ART D...  
6  {'流动的盛宴': 4, '如果这是宋史2·太宗、真宗卷': 3, '如果这是宋史': 3,...  
7  {'爱情、疯狂和死亡的故事': 5, '经验的重构': 4, '公共艺术教育研究': 2, ...  
8  {'动物园': 3, '请照顾好我妈妈': 3, '伊春': 2, '成为波伏瓦': 4, ...  
9  {'我的作文评改举隅': 4, '铃木大拙说禅': 4, '北平历史地理': 4, '《标点...

In [3]:
#这份是自己爬取的用户数据
users_2 = pd.read_csv(r'useres.csv')
users_2.head(10)

id        nickname  read_num  \
0   10258808             黑暗之刺      1304   
1    1070044               树上       426   
2    1109340         yuanyuan       342   
3  117701550               茶瑟       137   
4  120470431         Oliviauu       363   
5  121199275               dd        60   
6  122586304            网友陶女士       110   
7  126272087   dxysjfokdhcysf       167   
8  129346572              阿苏勒        17   
9  129817884            赤朽叶流名       535   

                                 read_book_and_score  
0  {'雪光之下': '4', '死亡藍調': '4', '狼時刻': '4', '暗夜与黎明'...  
1  {'排队': '2', '马可瓦尔多': '2', '逃避自由': '2', '如何解读中世...  
2  {'失踪的孩子': '5', '离开的，留下的': '5', '新名字的故事': '5', ...  
3  {'幸福的都市栖居': '4', '蛤蟆先生去看心理医生': '4', '逍遥游': '4'...  
4  {'你的灯亮着吗?': '4', '千年一叹': '4', '中国小品建筑十讲（插图珍藏本）...  
5  {'进化心理学(第4版)': '4', 'Python深度学习': '4', 'Fundam...  
6  {'胭脂扣': '3', '无人生还': '3', '金色梦乡': '3', '博尔赫斯：最...  
7  {'我与地坛': '4', '霍乱时期的爱情': '4', '海风中失落的血色馈赠': '4...  
8  {'上海堡垒': '3', '你若爱，生活哪里都可爱': '3', '偷影子的人': '3'...  
9  {'第十三个故事': '3', '九云梦': '3', '忏悔录': '3', 'チェンソー...

In [4]:
#将两个数据合并
users = pd.concat([users_1,users_2],axis = 0, ignore_index=True)
users

id       nickname  read_num  \
0            1000287           耶律王其        95   
1            1023147            殊不方       206   
2          103031697           一潭死水       115   
3            1032498            蜜三刀       631   
4          113496629          虫子凹二千       146   
..               ...            ...       ...   
940      zntoborges             支离疏      1060   
941            zona           chloe        87   
942        zshowing   ShowingV1.4.1       550   
943      zyrdolphin         YirAn怡然       171   
944  zzh1644hiraeth             张汝荪       266   

                                   read_book_and_score  
0    {'牧齋有學集（全三冊）': 4, '回鹘文买卖契约译注': 3, '清朝统一准噶尔史实研究...  
1    {'卡斯蒂利亚的田野：马查多诗选': 2, '艾吕雅诗选': 2, '想象一朵未来的玫瑰':...  
2    {'波斯人信札': 4, '阿马罗神父的罪恶': 4, '理智与情感（木刻插图本）': 4,...  
3    {'牲人祭': 3, '正定歌谣': 5, '中国民族史（上册）': 5, '地狱书单': ...  
4    {'救猫咪': 4, '牧羊少年奇幻之旅': 3, '月亮与六便士': 5, '山海经': ...  
..                                                 ...  
940  {'如何读，为什么读': '4', '中国传统文化十五讲': '4', '歧路灯/中国古典文...  
941  {'看见': '4', '哲学的慰藉': '4', '巨流河': '4', '寻路中国': ...  
942  {'处在十字路口的选择': '5', '贸易打造的世界': '5', '小王子': '5',...  
943  {'萤火虫女孩': '2', '雪娃娃': '2', '风娃娃': '2', '根娃娃': ...  
944  {'东方学': '5', '知识分子论': '5', '社会学家与历史学家': '5', '...  

[945 rows x 4 columns]

# 数据筛选

In [5]:
#更换数据类型便于后期计算
users['read_num'] = users['read_num'].astype("int32")
users.info()
users.describe()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 945 entries, 0 to 944
Data columns (total 4 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   id                   945 non-null    object
 1   nickname             945 non-null    object
 2   read_num             945 non-null    int32 
 3   read_book_and_score  945 non-null    object
dtypes: int32(1), object(3)
memory usage: 26.0+ KB


read_num
count  9.450000e+02
mean   7.615776e+04
std    2.328535e+06
min    3.000000e+00
25%    1.090000e+02
50%    2.280000e+02
75%    5.050000e+02
max    7.158156e+07

In [6]:
#筛去阅读数量小于50和大于5000的用户
users = users.drop(users[(users['read_num']<50) | (users['read_num'] > 5000)].index)
users

id       nickname  read_num  \
0            1000287           耶律王其        95   
1            1023147            殊不方       206   
2          103031697           一潭死水       115   
3            1032498            蜜三刀       631   
4          113496629          虫子凹二千       146   
..               ...            ...       ...   
940      zntoborges             支离疏      1060   
941            zona           chloe        87   
942        zshowing   ShowingV1.4.1       550   
943      zyrdolphin         YirAn怡然       171   
944  zzh1644hiraeth             张汝荪       266   

                                   read_book_and_score  
0    {'牧齋有學集（全三冊）': 4, '回鹘文买卖契约译注': 3, '清朝统一准噶尔史实研究...  
1    {'卡斯蒂利亚的田野：马查多诗选': 2, '艾吕雅诗选': 2, '想象一朵未来的玫瑰':...  
2    {'波斯人信札': 4, '阿马罗神父的罪恶': 4, '理智与情感（木刻插图本）': 4,...  
3    {'牲人祭': 3, '正定歌谣': 5, '中国民族史（上册）': 5, '地狱书单': ...  
4    {'救猫咪': 4, '牧羊少年奇幻之旅': 3, '月亮与六便士': 5, '山海经': ...  
..                                                 ...  
940  {'如何读，为什么读': '4', '中国传统文化十五讲': '4', '歧路灯/中国古典文...  
941  {'看见': '4', '哲学的慰藉': '4', '巨流河': '4', '寻路中国': ...  
942  {'处在十字路口的选择': '5', '贸易打造的世界': '5', '小王子': '5',...  
943  {'萤火虫女孩': '2', '雪娃娃': '2', '风娃娃': '2', '根娃娃': ...  
944  {'东方学': '5', '知识分子论': '5', '社会学家与历史学家': '5', '...  

[831 rows x 4 columns]

In [7]:
#根据用户阅读数量排序，查看一下结果
users = users.sort_values(by=['read_num'], ignore_index=True)
users

id  nickname  read_num  \
0            64032752        小过        50   
1             4860595      50PB        50   
2           49250057      木（已成柴        51   
3           198705077        云深        51   
4    juanjuandetudou         棉花        51   
..                ...       ...       ...   
826           3347336  dormouse      2948   
827         45304596         KD      2992   
828        liudaxian       青年哪吒      4073   
829      pinjarivera          暁      4541   
830         191290601  APTX4869      4869   

                                   read_book_and_score  
0    {'湯神くんには友達がいない 13': 5, '湯神くんには友達がいない 15': 5, '...  
1    {'卡明斯诗选': 4, '用电影燃尽欲望': 5, '教育七律': 3, '电影化叙事':...  
2    {'月亮和六便士': '1', '康巴情书': '1', '少有人走的路': '1', '吸...  
3    {'浮世画家': 3, '如梦之梦': 5, '莫失莫忘': 5, '长日将尽': 4, '...  
4    {'她世界': '4', '长不大的父母': '4', '心理治疗如何改变人': '4', ...  
..                                                 ...  
826  {'第三帝国的到来': 4, '克拉拉与太阳': 3, '镇魂': 2, '跷跷板妖怪': ...  
827  {'观念生物学': '4', '创造自然': '4', 'セックスセールスドライバー': '...  
828  {'暗知识：机器认知如何颠覆商业和社会': '3', '马背上的朝廷': '3', '侨易学...  
829  {'纨绔': '4', '旧宫殿': '4', '大唐兴亡三百年（全7册）': '4', '...  
830  {'皮皮鲁和神秘汽车': 1, '皮皮鲁和魔筷': 2, '蝲蛄吟唱的地方': 4, '爱你...  

[831 rows x 4 columns]

In [9]:
#删重、去掉无用数据
users = users.drop_duplicates(['id'], keep='first',ignore_index=True)
users = users.drop(['nickname', 'read_num'], axis = 1)
users

id                                read_book_and_score
0            64032752  {'湯神くんには友達がいない 13': 5, '湯神くんには友達がいない 15': 5, '...
1             4860595  {'卡明斯诗选': 4, '用电影燃尽欲望': 5, '教育七律': 3, '电影化叙事':...
2           49250057   {'月亮和六便士': '1', '康巴情书': '1', '少有人走的路': '1', '吸...
3           198705077  {'浮世画家': 3, '如梦之梦': 5, '莫失莫忘': 5, '长日将尽': 4, '...
4    juanjuandetudou   {'她世界': '4', '长不大的父母': '4', '心理治疗如何改变人': '4', ...
..                ...                                                ...
826           3347336  {'第三帝国的到来': 4, '克拉拉与太阳': 3, '镇魂': 2, '跷跷板妖怪': ...
827         45304596   {'观念生物学': '4', '创造自然': '4', 'セックスセールスドライバー': '...
828        liudaxian   {'暗知识：机器认知如何颠覆商业和社会': '3', '马背上的朝廷': '3', '侨易学...
829      pinjarivera   {'纨绔': '4', '旧宫殿': '4', '大唐兴亡三百年（全7册）': '4', '...
830         191290601  {'皮皮鲁和神秘汽车': 1, '皮皮鲁和魔筷': 2, '蝲蛄吟唱的地方': 4, '爱你...

[831 rows x 2 columns]

# 提取用户评分信息

In [13]:
a = users['read_book_and_score'].values
b = users['id'].values
data = pd.read_csv(r'book_dealed.csv')

In [14]:
i = 0
u = []
#用正则表达式将书籍与评分提取出来
try:
    for i in range(len(a)):
        booknames = []
        scores = []
        id_ = []
        book_name = re.findall("'(.*?)':", a[i])
        score = re.findall(":(.*?),", a[i], re.S)
        j = 0
        
        #先用字典存放，然后字典转dataframe便于后续操作
        for j in range(min(len(score), len(book_name))):
            score[j] = score[j].replace(" ", "")
            score[j] = score[j].replace("'", "")
            booknames.append(book_name[j])
            scores.append(score[j])
            id_.append(b[i])
        user = {'id':id_, 'book_name':booknames, 'score':scores}
        user = pd.DataFrame(user)
        name = user['book_name'].values.tolist()
        test = user
        
        #将不在我们爬取的书籍信息中的书去除，将所有dataframe放进列表中存起来
        try:
            k = 0
            for k in range(min(len(score), len(book_name))):
                results = data[(data['BOOK_NAME'] == name[k])]
                if len(results) == 0:
                    test = test.drop(user[user['book_name'] == name[k]].index)
            if not test.empty:
                u.append(test) 
        except Exception as e:
            pass
            print(e)
            
except Exception as e:
            pass
            print(e)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [15]:
len(u)

601

In [ ]:
#将所有的dataframe连在一起
readers = u[0]
i = 1
for i in range(len(u)):
    readers = pd.concat([readers,u[i]],axis = 0, ignore_index=True)

In [20]:
#经过一系列操作，最终得到了以下的dataframe，每一条都是用户的信息，后面便于变成透视表进行相似度计算
readers
rating = readers['score'].values
_id = readers['id'].values
_bookname = readers['book_name'].values
len(rating)

id  book_name score
0       64032752   爆漫王。(01)     5
1       64032752       无缘社会     4
2       64032752    把时间当作朋友     4
3       64032752  禅与摩托车维修艺术     4
4       64032752         精进     5
...          ...        ...   ...
39699  191290601   福尔摩斯探案全集     5
39700  191290601         恶意     5
39701  191290601         幻夜     2
39702  191290601       假面山庄     5
39703  191290601       无尽长夜     2

[39704 rows x 3 columns]

39704

In [ ]:
#这时候发现正则提取出来的评分数据不是很干净，有些不是纯数字，再次进行清洗
reader = readers
i = 0
for i in range(39704):
    try:
        check = re.search('(.*)', rating[i])
        check = check.group(1)
        if len(check) > 1:
            reader = reader.drop(readers[(readers['id'] == _id[i]) & (readers['book_name'] == _bookname[i])] .index)
    except Exception as e:
        print(e)

In [37]:
reader['score'] = reader['score'].astype('int32')
reader

id  book_name  score
0       64032752   爆漫王。(01)      5
1       64032752       无缘社会      4
2       64032752    把时间当作朋友      4
3       64032752  禅与摩托车维修艺术      4
4       64032752         精进      5
...          ...        ...    ...
39699  191290601   福尔摩斯探案全集      5
39700  191290601         恶意      5
39701  191290601         幻夜      2
39702  191290601       假面山庄      5
39703  191290601       无尽长夜      2

[39691 rows x 3 columns]

In [38]:
#透视表get
readers_matrix = pd.pivot_table(reader, index = ['id'], columns = ['book_name'], values = 'score')
readers_matrix

book_name        10 count (第1集)  100个基本  100天后会死的鳄鱼君  100颗子弹1  10人以下小团队管理手册  \
id                                                                            
1000287                     NaN     NaN          NaN      NaN           NaN   
1023147                     NaN     NaN          NaN      NaN           NaN   
103031697                   NaN     NaN          NaN      NaN           NaN   
1032498                     NaN     NaN          NaN      NaN           NaN   
1109340                     NaN     NaN          NaN      NaN           NaN   
...                         ...     ...          ...      ...           ...   
znsq                        NaN     NaN          NaN      NaN           NaN   
zona                        NaN     NaN          NaN      NaN           NaN   
zxyang                      NaN     4.0          NaN      NaN           3.0   
zycbat                      NaN     5.0          NaN      NaN           NaN   
zzh1644hiraeth              NaN     NaN          NaN      NaN           NaN   

book_name        11字谜案  13 67  150cm Life  1984  1988：我想和这个世界谈谈  ...  龍紋身的女孩  \
id                                                               ...           
1000287            NaN    NaN         NaN   NaN             NaN  ...     NaN   
1023147            NaN    NaN         NaN   NaN             NaN  ...     NaN   
103031697          NaN    NaN         NaN   NaN             NaN  ...     NaN   
1032498            NaN    NaN         NaN   NaN             NaN  ...     NaN   
1109340            NaN    NaN         NaN   NaN             NaN  ...     NaN   
...                ...    ...         ...   ...             ...  ...     ...   
znsq               NaN    NaN         NaN   NaN             NaN  ...     NaN   
zona               NaN    NaN         NaN   NaN             NaN  ...     NaN   
zxyang             NaN    NaN         NaN   NaN             NaN  ...     NaN   
zycbat             NaN    NaN         NaN   NaN             NaN  ...     NaN   
zzh1644hiraeth     NaN    NaN         NaN   NaN             NaN  ...     NaN   

book_name        龙与地下铁  龙头凤尾  龙文身的女孩  龙族Ⅰ  龙族Ⅱ  龙族Ⅲ  龙族Ⅳ  龙王闹海  龙珠1  
id                                                                   
1000287            NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
1023147            NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
103031697          NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
1032498            NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
1109340            NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
...                ...   ...     ...  ...  ...  ...  ...   ...  ...  
znsq               NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
zona               NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
zxyang             NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
zycbat             NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  
zzh1644hiraeth     NaN   NaN     NaN  NaN  NaN  NaN  NaN   NaN  NaN  

[601 rows x 3655 columns]

In [45]:
readers_matrix.shape[0]

601

In [84]:
#小试了一下隐语义的模型，但是它的迭代时间实在是太久了，而且数据提取好像不是很方便，放弃了
# def LFM(R, alpha, lambda_, epoch, K):
#     M = R.shape[0]
#     N = R.shape[1]
    
#     P = np.random.rand(M, K)
#     Q = np.random.rand(N, K)
#     Q = Q.T
    
#     for step in range(epoch):
#         for u in range(M):
#             for i in range(N):
#                 if R[u][i] > 0:
#                     eui = np.dot(P[u,:], Q[:,i]) - R[u][i]
#                     for k in range(K):
#                         P[u][k] = P[u][k] - alpha * 2 * (eui * Q[k][i] + lambda_ * P[u][k])
#                         Q[k][i] = Q[k][i] - alpha * 2 * (eui * P[u][k] + lambda_ * Q[k][i])
#                 alpha *= 0.9

#     return P, Q

In [222]:
# K = 2
# alpha = 0.01
# lambda_ = 0.2
# epoch = 100
# M = readers_matrix.fillna(0)
# A,B = LFM(M.values, alpha, lambda_, epoch, K)
# A
# B

In [223]:
# np.dot(A, B)

In [243]:
#把整理出来的数据存进mysql
conn = pymysql.connect( 
    host="localhost",
    user="root",
    password="YUAN69188059*", 
    database="douban",
    charset="utf8"
)

cursor = conn.cursor()

In [244]:
sql = """CREATE TABLE READERS (
                     id TEXT,
                     book_name TEXT,
                     score TEXT
                     )"""
try:
    cursor.execute(sql)
except Exception as e:
    print(e)
    conn.rollback()
cursor = conn.cursor()

0

In [245]:
Id = reader['id'].values.tolist()
Book_name = reader['book_name'].values.tolist()
Score = reader['score'].values
Score.dtype
len(Score)

dtype('int32')

39691

In [246]:
for i in range(39691):
    sql = """
        INSERT INTO READERS(id, book_name, score)
        VALUES(%s, %s, %s)
    """
    data = [(Id[i], Book_name[i], Score[i])]
    try:
        cursor.executemany(sql, data)
        conn.commit()
    except Exception as e:
        print(e)
        conn.rollback()

1

1

1

1

1

...

1

1

1

1

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

